In [3]:
import datetime as dt
import pandas as pd
import numpy as np 

from pandas_datareader import data as pdr
import plotly.offline as pyo
import plotly.graph_objects as go
from plotly.subplots import make_subplots

pyo.init_notebook_mode(connected=True)
pd.options.plotting.backend = 'plotly'

**Get stock data with pandas_datareader**

In [4]:
end = dt.datetime.now()
start = dt.datetime(2015,1,1)

df = pdr.get_data_yahoo(['^AXJO','CBA.AX','NAB.AX','STO.AX'],start, end)
Close = df.Close
Close.head()

Symbols           ^AXJO     CBA.AX     NAB.AX    STO.AX
Date                                                   
2015-01-01  5435.899902  85.277962  31.925041  7.132698
2015-01-04  5450.299805  85.486832  31.972605  7.193661
2015-01-05  5364.799805  84.840332  31.715757  6.575320
2015-01-06  5353.600098  84.651360  31.791861  6.488230
2015-01-07  5381.500000  84.929848  32.077248  6.357594

**Compute log returns**

In [5]:
log_returns = np.log(df.Close/df.Close.shift(1)).dropna()

**Calculate daily standard deviation of returns**

In [6]:
daily_std = log_returns.std()
daily_std 

Symbols
^AXJO     0.010285
CBA.AX    0.014472
NAB.AX    0.015203
STO.AX    0.028363
dtype: float64

In [7]:
annualized_std = daily_std * np.sqrt(252)  ## 252 trading days in the year
annualized_std * 100

Symbols
^AXJO     16.326923
CBA.AX    22.973323
NAB.AX    24.133635
STO.AX    45.024269
dtype: float64

**Plot histogram of log returns with annualized volatility**

In [8]:
fig = make_subplots(rows=2, cols=2)
trace0 = go.Histogram(x=log_returns['CBA.AX'], name='CBA')
trace1 = go.Histogram(x=log_returns['NAB.AX'], name='NAB')
trace2 = go.Histogram(x=log_returns['STO.AX'], name='STO')

fig.append_trace(trace0, 1, 1)
fig.append_trace(trace1, 1, 2)
fig.append_trace(trace2, 2, 1)

fig.update_layout(autosize = False, width=700, height=600, title='Frequency of log returns',
                  xaxis=dict(title='CBA Annualized Volatility: ' + str(np.round(annualized_std['CBA.AX']*100, 1))),
                  xaxis2=dict(title='NAB Annualized Volatility: ' + str(np.round(annualized_std['NAB.AX']*100, 1))),
                  xaxis3=dict(title='STO Annualized Volatility: ' + str(np.round(annualized_std['STO.AX']*100, 1))),
                  )
fig.show()

**Trailing volatility over time**

In [9]:
TRADING_DAYS = 60
volatility = log_returns.rolling(window=TRADING_DAYS).std() * np.sqrt(TRADING_DAYS)

In [10]:
volatility.plot().update_layout(autosize = False, width=600, height=300).show()

**Sharpe Ratio**

In [11]:
Rf = 0.01/252
sharpe_ratio = (log_returns.rolling(window=TRADING_DAYS).mean() - Rf)*TRADING_DAYS/volatility
sharpe_ratio.dropna()

Symbols        ^AXJO    CBA.AX    NAB.AX    STO.AX
Date                                              
2015-03-29  1.128638  0.953706  2.044123 -0.757918
2015-03-30  1.203987  0.962742  2.111136 -0.714870
2015-03-31  1.420020  1.048840  2.210382 -0.465183
2015-04-01  1.558310  1.206227  2.273706 -0.380222
2015-04-07  1.549822  1.142159  2.346871 -0.159349
...              ...       ...       ...       ...
2022-06-29 -1.356089 -1.187142 -1.220920 -0.195712
2022-06-30 -1.547254 -1.306818 -1.399033 -0.448170
2022-07-01 -1.629612 -1.206583 -1.294592 -0.651864
2022-07-04 -1.507586 -1.186322 -1.250242 -0.574391
2022-07-05 -1.420101 -1.333219 -1.384428 -0.481801

[1835 rows x 4 columns]

In [12]:
sharpe_ratio.plot().update_layout(autosize=False,width=600,height=300)

**Sortino Ratio**

In [16]:
sortino_vol = log_returns[log_returns < 0].rolling(window=TRADING_DAYS, center=True, min_periods=10).std() * np.sqrt(TRADING_DAYS)
sortino_ratio = (log_returns.rolling(window=TRADING_DAYS).mean() - Rf)*TRADING_DAYS/sortino_vol

In [17]:
sortino_vol.plot().update_layout(autosize = False, width=600, height=300)

In [18]:
sortino_ratio.plot().update_layout(autosize = False, width=600, height=300)

**Modigliani ratio (M2 ratio)**

In [19]:
m2_ratio = pd.DataFrame()
benchmark_vol = volatility['^AXJO']

for c in log_returns.columns:
    if c != '^AXJO':
        m2_ratio[c] = (sharpe_ratio[c] * benchmark_vol / TRADING_DAYS + Rf) * TRADING_DAYS

In [20]:
m2_ratio.plot().update_layout(autosize = False, width=600, height=300)

**Max Drawdown**

In [23]:
def max_drawdown(returns):
    cumulative_returns = (1 + returns).cumprod()
    peak = cumulative_returns.expanding(min_periods = 1).max()  ## to find the absolute peak of this cumulative returns series
    drawdown = (cumulative_returns/peak) - 1
    return drawdown.min()



returns = df.Close.pct_change().dropna()
max_drawdowns = returns.apply(max_drawdown, axis=0)
max_drawdowns * 100

Symbols
^AXJO    -36.530541
CBA.AX   -43.361732
NAB.AX   -63.126540
STO.AX   -69.444444
dtype: float64

**Calmar ratio**

In [26]:
calmars = np.exp(log_returns.mean()*252) / abs(max_drawdowns)
calmars.plot.bar().update_layout(autosize = False, width=600, height=300)
